In [4]:
import ipynb.fs.full.helper as h

from imp import reload
reload(h)

<module 'ipynb.fs.full.helper' (/tf/src/scripts/helper.ipynb)>

In [5]:
import cv2, os
import matplotlib.pyplot as plt
import numpy as np
from retinaface import RetinaFace
from tensorflow import keras
import ffmpeg

In [6]:
def paint(in_frame, preds, corrected_outputs):
    resultIMG = in_frame
    
    for i, pred in enumerate(preds):
        (startX, startY, endX, endY) = pred[0]
        output = corrected_outputs[i]
        
        y_classes = output.argmax(axis=-1)
        prob = output[0][y_classes][0]       
        label = query_array[y_classes[0]]
    
        cv2.rectangle(resultIMG, (startX, startY), (endX, endY), (0, 0, 255), 2)
        cv2.putText(resultIMG, f'{label}: ' + "{:.4}".format(float(prob)) , 
                                    (startX, startY-10), cv2.FONT_HERSHEY_SIMPLEX, 1, colorPercentage(prob),2)
    
    return resultIMG

In [7]:
def analyse2(in_filename, out_filename):
    
    probe = ffmpeg.probe(in_filename)
    height = probe['streams'][0]['height']
    width = probe['streams'][0]['width']
    nb_frames = probe['streams'][0]['nb_frames'] 
    
    process1 = (
    ffmpeg
    .input(in_filename)
    .output('pipe:', format='rawvideo', pix_fmt='rgb24', vframes=nb_frames)
    .run_async(pipe_stdout=True)
    )

    process2 = (
    ffmpeg
    .input('pipe:', format='rawvideo', pix_fmt='rgb24', s='{}x{}'.format(width, height))
    .output(out_filename, pix_fmt='yuv420p')
    .overwrite_output()
    .run_async(pipe_stdin=True)
    )
    
    #cost = 0.5
    i = 0
    timeline = []
    
    while True:
        in_bytes = process1.stdout.read(width * height * 3)
        if not in_bytes:
            break
        in_frame = (
            np
            .frombuffer(in_bytes, np.uint8)
            .reshape([height, width, 3])
        )

        # Analyse
        preds = detect5(in_frame)
        
        corrected_outputs = None
        if i > 0:
            corrected_outputs = []
            for present_face in preds:
                corrected_output = present_face[1] * 1
                j = 1
                for k, step in enumerate(reversed(timeline)):
                    for past_pred in step:
                        if get_iou(present_face[0], past_pred[0]) > 0.5:
                            corrected_output += past_pred[1] #* cost ** k + 1
                            j += 1 #* cost ** (k + 1)
                corrected_output /= j
                corrected_outputs.append(corrected_output)
            
        timeline.append(preds)
        i += 1
        
        if corrected_outputs == None:
            corrected_outputs = list(zip(*preds))[1]
            
        
        out_frame = paint(in_frame, preds, corrected_outputs)
                        

        process2.stdin.write(
            out_frame
            .astype(np.uint8)
            .tobytes()
        )

    process2.stdin.close()
    process1.wait()
    process2.wait()

In [8]:
# https://stackoverflow.com/questions/25349178/calculating-percentage-of-bounding-box-overlap-for-image-detector-evaluation

def get_iou(bb1, bb2):
    """
    Calculate the Intersection over Union (IoU) of two bounding boxes.

    Parameters
    ----------
    bb1 : dict
        Keys: {'x1', 'x2', 'y1', 'y2'}
        The (x1, y1) position is at the top left corner,
        the (x2, y2) position is at the bottom right corner
    bb2 : dict
        Keys: {'x1', 'x2', 'y1', 'y2'}
        The (x, y) position is at the top left corner,
        the (x2, y2) position is at the bottom right corner

    Returns
    -------
    float
        in [0, 1]
    """
    
    print(bb1)
    bb1 = list(bb1)
    bb2 = list(bb2)
    
    bb1 = {
        "x1": bb1[0],
        "y1": bb1[1],
        "x2": bb1[2],
        "y2": bb1[3]
    }
    
    bb2 = {
        "x1": bb2[0],
        "y1": bb2[1],
        "x2": bb2[2],
        "y2": bb2[3]
    }
    
    assert bb1['x1'] < bb1['x2']
    assert bb1['y1'] < bb1['y2']
    assert bb2['x1'] < bb2['x2']
    assert bb2['y1'] < bb2['y2']

    # determine the coordinates of the intersection rectangle
    x_left = max(bb1['x1'], bb2['x1'])
    y_top = max(bb1['y1'], bb2['y1'])
    x_right = min(bb1['x2'], bb2['x2'])
    y_bottom = min(bb1['y2'], bb2['y2'])

    if x_right < x_left or y_bottom < y_top:
        return 0.0

    # The intersection of two axis-aligned bounding boxes is always an
    # axis-aligned bounding box
    intersection_area = (x_right - x_left) * (y_bottom - y_top)

    # compute the area of both AABBs
    bb1_area = (bb1['x2'] - bb1['x1']) * (bb1['y2'] - bb1['y1'])
    bb2_area = (bb2['x2'] - bb2['x1']) * (bb2['y2'] - bb2['y1'])

    # compute the intersection over union by taking the intersection
    # area and dividing it by the sum of prediction + ground-truth
    # areas - the interesection area
    iou = intersection_area / float(bb1_area + bb2_area - intersection_area)
    assert iou >= 0.0
    assert iou <= 1.0
    return iou

In [9]:
# adjust image darker and light 
adjust_light,rows,cols = 2.2,3,2
#igure= plt.figure(figsize = (14,14))
axes = []
assign = {'0':'Mask','1':"No Mask"}
face_list = [] # save no mask


def detect5(in_frame):
    #print(in_frame)
    try:
        image = in_frame
        resultIMG = in_frame
        
        back_image = image
        image = cv2.LUT(image.astype(np.uint8), np.array([((i / 255.0) ** (1.0 / adjust_light)) * 255 for i in np.arange(0, 256)]).astype(np.uint8))
        blob = cv2.dnn.blobFromImage(image=cv2.resize(image, (300,300)), scalefactor=1.0, size=(300, 300), mean=(104.0, 177.0, 123.0))
       
        OC_Net.setInput(blob)
        detections = OC_Net.forward()
        length = detections.shape[2]
        (height, width) = image.shape[:2]
        
        faces = []
                        
        for i in range(0, length):
            
            # get the face box
            boxs = detections[0, 0, i, 3:7] * np.array([width, height, width, height])
            (startX, startY, endX, endY) = boxs.astype("int")
            
            
            
            #print((startX, startY, endX, endY))
            frame = image[startY:endY, startX:endX]
            #print(frame)
        
            # according to the confidence_threshold, to get the lable
            confidence_threshold = detections[0, 0, i, 2]
            if confidence_threshold > 0.2:
                #rint(img_size)
                #print(frame[0])
                label_Y,result = get_label(frame,img_size)
                #rint(label_Y,result)
                
                if (label_Y == 1):
                    frame = cv2.resize(frame,(224,224))
                    frame = np.reshape(frame,[1,224,224,3])/255.0
                    y_prob = classifier.predict(frame)
                    
                    
                    face = ((startX, startY, endX, endY), y_prob)
                    faces.append(face)
        
        return faces
        
    except ValueError:
        print(ValueError)
        print(framePath + frame)
        
    except Exception as e:
        print(e)
        return []
        
    except TypeError:
        return in_frame

In [18]:
def extract_face(face):
    # resize pixels to the model size
    image = Image.fromarray(face)
    image = image.resize(required_size)
    face_array = np.asarray(image)
    return face_array

def get_label(frame,img_size):
    im = cv2.resize(frame,(img_size,img_size))
    im = np.array(im)/255.0
    im = im.reshape(1,img_size,img_size,3)
    result = model.predict(im)
    label_Y=1 if result>0.3 else 0
    return label_Y,result

In [27]:
def colorPercentage(pct):
    pct_diff = 1.0 - pct
    r = min(255, pct_diff*2 * 255)
    g = min(255, pct*2 * 255)
    return (r, g, 0)

In [28]:
# TODO
model = keras.models.load_model(f"{h.abspath}/NewMaskODM/models/v2/")
classifier = keras.models.load_model(f'{h.abspath}/models/classification/newClass/v9/v6/') #v6

OC_Net = cv2.dnn.readNetFromCaffe(f"{h.abspath}/NewMaskODM/caffe/architecture.txt", f'{h.abspath}/NewMaskODM/caffe/weights.caffemodel')
img_size = h.img_size
query_array = h.celeb_array

In [29]:
file_name = "merkel2.mp4"

file_path = h.testsOptVideos + "/" + file_name
file_out = h.testsOptVideos + "/" + f'OUT_{file_name}'


In [30]:
analyse2(file_path, file_out)

(398, 91, 520, 252)
(397, 91, 520, 253)
(397, 91, 520, 253)
(392, 90, 514, 251)
(392, 90, 514, 251)
(392, 90, 514, 251)
(392, 91, 515, 250)
(392, 91, 515, 250)
(392, 91, 515, 250)
(392, 91, 515, 250)
(391, 93, 514, 250)
(391, 93, 514, 250)
(391, 93, 514, 250)
(391, 93, 514, 250)
(391, 93, 514, 250)
(390, 94, 515, 250)
(390, 94, 515, 250)
(390, 94, 515, 250)
(390, 94, 515, 250)
(390, 94, 515, 250)
(390, 94, 515, 250)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 513, 251)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 94, 512, 250)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 95, 513, 251)
(391, 100, 513, 253)
(391, 100, 513, 253)
(391, 100, 513, 253)
(391, 100, 513, 253)
(391, 100, 513, 

(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 102, 521, 253)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 522, 254)
(397, 97, 5

(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(388, 102, 509, 251)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 510, 254)
(387, 104, 51

(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)
(385, 97, 502, 243)


(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 504, 258)
(384, 110, 50

...

(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 517, 274)
(406, 109, 51

(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 517, 271)
(406, 107, 51

(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 520, 270)
(400, 102, 52

(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 521, 268)
(400, 100, 52

(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
(406, 95, 522, 262)
